# Project 03 - Crime

In [1]:
from datetime import datetime
import pandas as pd
import json
import pprint
import logging
from pymongo import MongoClient
logging.basicConfig(level=logging.DEBUG, format='%(asctime)s -  %(levelname)s -  %(message)s')
logging.debug('Start of program')
# logging.disable(logging.CRITICAL) # Uncomment when done debugging.

2024-07-16 21:13:46,775 -  DEBUG -  Start of program


In [2]:
try:
    dataset = pd.read_csv("CMPD_Incidents_raw_data.csv")
    logging.debug("Dataset loaded in successfully.")
    dataset.head()
except:
    logging.error("Dataset failed to be read in to pandas dataframe.")

2024-07-16 21:13:48,509 -  DEBUG -  Dataset loaded in successfully.


In [3]:
dataset.dtypes

X                              int64
Y                            float64
YEAR                           int64
INCIDENT_REPORT_ID            object
LOCATION                      object
CITY                          object
STATE                         object
ZIP                          float64
X_COORD_PUBLIC                 int64
Y_COORD_PUBLIC                 int64
LATITUDE_PUBLIC              float64
LONGITUDE_PUBLIC             float64
DIVISION_ID                   object
CMPD_PATROL_DIVISION          object
NPA                            int64
DATE_REPORTED                 object
DATE_INCIDENT_BEGAN           object
DATE_INCIDENT_END             object
ADDRESS_DESCRIPTION           object
LOCATION_TYPE_DESCRIPTION     object
PLACE_TYPE_DESCRIPTION        object
PLACE_DETAIL_DESCRIPTION      object
CLEARANCE_STATUS              object
CLEARANCE_DETAIL_STATUS       object
CLEARANCE_DATE                object
HIGHEST_NIBRS_CODE            object
HIGHEST_NIBRS_DESCRIPTION     object
O

In [4]:
logging.debug("Our chosen columns to filter for our dataset.")
cols = ["YEAR",
        "LOCATION",
        "LATITUDE_PUBLIC",
        "LONGITUDE_PUBLIC",
        "CMPD_PATROL_DIVISION",
        "DATE_REPORTED",
        "ADDRESS_DESCRIPTION",
        "LOCATION_TYPE_DESCRIPTION",
        "PLACE_TYPE_DESCRIPTION",
        "PLACE_DETAIL_DESCRIPTION",
        "CLEARANCE_STATUS",
        "HIGHEST_NIBRS_DESCRIPTION",
        "OBJECTID"]

2024-07-16 21:13:48,543 -  DEBUG -  Our chosen columns to filter for our dataset.


In [5]:
logging.debug("Filtering out unneeded columns.")
dataset = dataset[cols]
dataset.head(2)

2024-07-16 21:13:48,560 -  DEBUG -  Filtering out unneeded columns.


YEAR             LOCATION  LATITUDE_PUBLIC  LONGITUDE_PUBLIC  \
0  2023  3500 STATESVILLE AV        35.266384        -80.837353   
1  2023           600 KEY ST        35.256409        -80.890667   

  CMPD_PATROL_DIVISION           DATE_REPORTED     ADDRESS_DESCRIPTION  \
0                Metro  2023/08/10 00:00:00+00  Location of occurrence   
1              Freedom  2023/09/14 00:00:00+00  Location of occurrence   

  LOCATION_TYPE_DESCRIPTION PLACE_TYPE_DESCRIPTION PLACE_DETAIL_DESCRIPTION  \
0                  Outdoors                 Retail        Convenience Store   
1                   Indoors            Residential        Private Residence   

    CLEARANCE_STATUS HIGHEST_NIBRS_DESCRIPTION  OBJECTID  
0  Cleared by Arrest        Aggravated Assault         4  
1  Cleared by Arrest            Simple Assault         5

In [6]:
logging.info(f"Dataframe has {dataset.shape[0]} rows and {dataset.shape[1]} columns.")

2024-07-16 21:13:48,666 -  INFO -  Dataframe has 144832 rows and 13 columns.


In [7]:
dataset["CLEARANCE_STATUS"].value_counts()

CLEARANCE_STATUS
Open                                   95939
Exceptionally Cleared                  25760
Cleared by Arrest                      16987
Unfounded                               4749
Cleared by Arrest by Another Agency     1397
Name: count, dtype: int64

In [8]:
logging.info("Filtering the 'CLEARANCE_STATUS' column to remove rows with 'Unfounded' as its value")
dataset = dataset[dataset["CLEARANCE_STATUS"] != "Unfounded"]
dataset.head()

2024-07-16 21:13:48,731 -  INFO -  Filtering the 'CLEARANCE_STATUS' column to remove rows with 'Unfounded' as its value


YEAR             LOCATION  LATITUDE_PUBLIC  LONGITUDE_PUBLIC  \
0  2023  3500 STATESVILLE AV        35.266384        -80.837353   
1  2023           600 KEY ST        35.256409        -80.890667   
2  2023     1900 RANDOLPH RD        35.210784        -80.824610   
3  2023       800 MCALWAY RD        35.189364        -80.793423   
4  2023       3300 DURHAM LN        35.294751        -80.838000   

  CMPD_PATROL_DIVISION           DATE_REPORTED     ADDRESS_DESCRIPTION  \
0                Metro  2023/08/10 00:00:00+00  Location of occurrence   
1              Freedom  2023/09/14 00:00:00+00  Location of occurrence   
2           Providence  2023/02/09 00:00:00+00  Location of occurrence   
3           Providence  2023/07/18 00:00:00+00  Location of occurrence   
4                North  2023/06/15 00:00:00+00  Location of occurrence   

  LOCATION_TYPE_DESCRIPTION  PLACE_TYPE_DESCRIPTION  \
0                  Outdoors                  Retail   
1                   Indoors             Residential   
2              Parking Deck  Public/Non-Residential   
3               Parking Lot             Residential   
4                   Indoors             Residential   

       PLACE_DETAIL_DESCRIPTION       CLEARANCE_STATUS  \
0             Convenience Store      Cleared by Arrest   
1             Private Residence      Cleared by Arrest   
2     Hospital/Medical Facility                   Open   
3  Apartment/Duplex Private Res                   Open   
4  Apartment/Duplex Private Res  Exceptionally Cleared   

  HIGHEST_NIBRS_DESCRIPTION  OBJECTID  
0        Aggravated Assault         4  
1            Simple Assault         5  
2       Motor Vehicle Theft         6  
3  Theft From Motor Vehicle         8  
4            Simple Assault        16

In [9]:
logging.debug("Reformatting date from 'yyyy/mm/dd 00:00:00+00' to 'mm/dd/yyyy'.")
dataset["DATE_REPORTED"] = dataset["DATE_REPORTED"].apply(
    lambda x: datetime.strptime(x.split(" ")[0], "%Y/%M/%d").strftime("%M-%d-%Y")
)

2024-07-16 21:13:48,830 -  DEBUG -  Reformatting date from 'yyyy/mm/dd 00:00:00+00' to 'mm/dd/yyyy'.


## Data cleaning

In [10]:
dataset.head(2)

YEAR             LOCATION  LATITUDE_PUBLIC  LONGITUDE_PUBLIC  \
0  2023  3500 STATESVILLE AV        35.266384        -80.837353   
1  2023           600 KEY ST        35.256409        -80.890667   

  CMPD_PATROL_DIVISION DATE_REPORTED     ADDRESS_DESCRIPTION  \
0                Metro    08-10-2023  Location of occurrence   
1              Freedom    09-14-2023  Location of occurrence   

  LOCATION_TYPE_DESCRIPTION PLACE_TYPE_DESCRIPTION PLACE_DETAIL_DESCRIPTION  \
0                  Outdoors                 Retail        Convenience Store   
1                   Indoors            Residential        Private Residence   

    CLEARANCE_STATUS HIGHEST_NIBRS_DESCRIPTION  OBJECTID  
0  Cleared by Arrest        Aggravated Assault         4  
1  Cleared by Arrest            Simple Assault         5

In [11]:
working_copy = dataset.copy()
x = working_copy.to_dict("records")
#pprint.pprint(x)

In [12]:
with open("dataset.json", "w") as outfile:
    json.dump(x, outfile, indent=4, sort_keys=False)

# Data Storing

In [13]:
mongo = MongoClient(port=27017)

In [14]:
db = mongo.Incidents
crime = db.crime

In [15]:
crime.insert_many(x)

2024-07-16 21:18:35,347 -  DEBUG -  {"message": "Server selection started", "selector": "<function writable_server_selector at 0x000002BDC196C220>", "operation": "insert", "operationId": -1191235325, "topologyDescription": "<TopologyDescription id: 66971ae2f203b2a89f0479dd, topology_type: Single, servers: [<ServerDescription ('localhost', 27017) server_type: Standalone, rtt: 0.0>]>", "clientId": {"$oid": "66971ae2f203b2a89f0479dd"}}
2024-07-16 21:18:35,349 -  DEBUG -  {"message": "Server selection succeeded", "selector": "<function writable_server_selector at 0x000002BDC196C220>", "operation": "insert", "operationId": -1191235325, "topologyDescription": "<TopologyDescription id: 66971ae2f203b2a89f0479dd, topology_type: Single, servers: [<ServerDescription ('localhost', 27017) server_type: Standalone, rtt: 0.0>]>", "clientId": {"$oid": "66971ae2f203b2a89f0479dd"}, "serverHost": "localhost", "serverPort": 27017}
2024-07-16 21:18:35,834 -  DEBUG -  {"clientId": {"$oid": "66971ae2f203b2a89

InsertManyResult([ObjectId('66971be9f203b2a89f0479de'), ObjectId('66971be9f203b2a89f0479df'), ObjectId('66971be9f203b2a89f0479e0'), ObjectId('66971be9f203b2a89f0479e1'), ObjectId('66971be9f203b2a89f0479e2'), ObjectId('66971be9f203b2a89f0479e3'), ObjectId('66971be9f203b2a89f0479e4'), ObjectId('66971be9f203b2a89f0479e5'), ObjectId('66971be9f203b2a89f0479e6'), ObjectId('66971be9f203b2a89f0479e7'), ObjectId('66971be9f203b2a89f0479e8'), ObjectId('66971be9f203b2a89f0479e9'), ObjectId('66971be9f203b2a89f0479ea'), ObjectId('66971be9f203b2a89f0479eb'), ObjectId('66971be9f203b2a89f0479ec'), ObjectId('66971be9f203b2a89f0479ed'), ObjectId('66971be9f203b2a89f0479ee'), ObjectId('66971be9f203b2a89f0479ef'), ObjectId('66971be9f203b2a89f0479f0'), ObjectId('66971be9f203b2a89f0479f1'), ObjectId('66971be9f203b2a89f0479f2'), ObjectId('66971be9f203b2a89f0479f3'), ObjectId('66971be9f203b2a89f0479f4'), ObjectId('66971be9f203b2a89f0479f5'), ObjectId('66971be9f203b2a89f0479f6'), ObjectId('66971be9f203b2a89f0479